In [ ]:
from keras import applications
from keras.preprocessing.image import ImageDataGenerator
from keras.preprocessing import image
from keras import optimizers
from keras.models import Sequential, Model 
from keras.layers import Dropout, Flatten, Dense, GlobalAveragePooling2D
from keras import backend as k 
from keras.callbacks import ModelCheckpoint, LearningRateScheduler, TensorBoard, EarlyStopping
from keras.applications.resnet50 import ResNet50
from keras.applications.inception_resnet_v2 import InceptionResNetV2
from keras.models import load_model
from keras.losses import mean_absolute_error
import tensorflow as tf
import os
import numpy as np
import cv2
import matplotlib.pyplot as plt
import pandas as pd
import math
from tqdm import tqdm
from keras.utils import plot_model

from lr_finder import LRFinder
from sgdr import SGDRScheduler
from xception import Xception

In [2]:
train_path = 'X:/Flipkart GRID - Object Localization (Medium Complexity Round)/augument_data/training_images'
npy_img_dir = 'X:/Flipkart GRID - Object Localization (Medium Complexity Round)\\augument_data\\training_images_batches'
architecture_plot_save_dir = 'X:/Flipkart GRID - Object Localization (Medium Complexity Round)/'

img_width, img_height = 299., 299.
rx = 2.1404
ry = 1.61

In [3]:
base_dir = 'X:/Flipkart GRID - Object Localization (Medium Complexity Round)/'
epochs = 1000
chkpt_dir = "X:/Flipkart GRID - Object Localization (Medium Complexity Round)/chkpts/xception_lrf_training_s3_data.h5"
data_s3_path = 'X:/Flipkart GRID - Object Localization (Medium Complexity Round)/data_s3/'

In [4]:
# base_model = Xception(include_top=False, weights=None, input_shape = (299, 299, 3), classes = 4)

In [5]:
# for layer in base_model.layers[:-3]:
#     layer.trainable= False

In [6]:
# x = base_model.output
# x = Flatten()(x)
# predictions = Dense(4, activation="relu")(x)

In [7]:
# model.load_weights("X:/Flipkart GRID - Object Localization (Medium Complexity Round)/chkpts/inceptionresnetv2_lrf_submission.h5")

In [8]:
def mIoU(labels,predictions):
    pred_x1=predictions[:,0]
    pred_x2=predictions[:,1]
    pred_y1=predictions[:,2]
    pred_y2=predictions[:,3]
    label_x1=labels[:,0]
    label_x2=labels[:,1]
    label_y1=labels[:,2]
    label_y2=labels[:,3]
    int_x1 = tf.maximum(pred_x1, label_x1)
    int_x2 = tf.minimum(pred_x2, label_x2)
    int_y1 = tf.maximum(pred_y1, label_y1)
    int_y2 = tf.minimum(pred_y2, label_y2)
    tensor_type = pred_x1.dtype
    pred_area = tf.multiply(tf.maximum(tf.cast(0.0, tensor_type), pred_x2 - pred_x1), tf.maximum(tf.cast(0.0, tensor_type), pred_y2 - pred_y1))
    label_area = tf.multiply(tf.maximum(tf.cast(0.0, tensor_type), label_x2 - label_x1), tf.maximum(tf.cast(0.0, tensor_type), label_y2 - label_y1))
    int_area = tf.multiply(tf.maximum(tf.cast(0.0, tensor_type), int_x2 - int_x1), tf.maximum(tf.cast(0.0, tensor_type), int_y2 - int_y1))
    union_area = pred_area + label_area - int_area
    IoU = int_area / union_area
    return tf.reduce_mean(IoU)

In [9]:
# model = Model(input = base_model.input, output = predictions)
model = load_model('X:/Flipkart GRID - Object Localization (Medium Complexity Round)/chkpts/xception_lrf_training_s3_data.h5', custom_objects = {'mIoU':mIoU})
model.summary()

__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_1 (InputLayer)            (None, 299, 299, 3)  0                                            
__________________________________________________________________________________________________
block1_conv1 (Conv2D)           (None, 149, 149, 32) 864         input_1[0][0]                    
__________________________________________________________________________________________________
block1_conv1_bn (BatchNormaliza (None, 149, 149, 32) 128         block1_conv1[0][0]               
__________________________________________________________________________________________________
block1_conv1_act (Activation)   (None, 149, 149, 32) 0           block1_conv1_bn[0][0]            
__________________________________________________________________________________________________
block1_con

block9_sepconv1 (SeparableConv2 (None, 19, 19, 728)  536536      block9_sepconv1_act[0][0]        
__________________________________________________________________________________________________
block9_sepconv1_bn (BatchNormal (None, 19, 19, 728)  2912        block9_sepconv1[0][0]            
__________________________________________________________________________________________________
block9_sepconv2_act (Activation (None, 19, 19, 728)  0           block9_sepconv1_bn[0][0]         
__________________________________________________________________________________________________
block9_sepconv2 (SeparableConv2 (None, 19, 19, 728)  536536      block9_sepconv2_act[0][0]        
__________________________________________________________________________________________________
block9_sepconv2_bn (BatchNormal (None, 19, 19, 728)  2912        block9_sepconv2[0][0]            
__________________________________________________________________________________________________
block9_sep

In [10]:
# IoU Metric Test
LABEL = [[0.0, 1.0, 0.0, 1.0], 
        [2.0, 3.0, 2.0, 3.0]]
PRED = [[0.5, 1.5, 0.5, 1.5],
        [2.0, 3.0, 2.0, 3.0]]
LABEL = tf.constant(np.array(LABEL))
PRED = tf.constant(np.array(PRED))
print(mIoU(LABEL, PRED))
with tf.Session() as sess:
    val = sess.run(mIoU(LABEL, PRED))
    print(val)

Tensor("Mean:0", shape=(), dtype=float64)
0.5714285714285714


#### Load best model weights from here, if required.

In [11]:
train_df = pd.read_csv(os.path.join(base_dir, 'orig_data', 'training_set_s3.csv'))
train_df.head()
# augment_val_df = pd.read_csv(os.path.join(base_dir, 'orig_data', 'augmented_val_data.csv'))

image_name   x1   x2   y1   y2
0             JPEG_20160517_140621_1000651031832.png   78  446   83  422
1                   1473231510890DeeplearnS11456.png   73  567  146  351
2                         1476881557883Untitled1.png   13  561  124  362
3  1474264827890cobalt-beyond-the-sea-maxi-dress3...    0  640  140  330
4             JPEG_20160711_113321_1000235741992.png  217  442   65  465

In [12]:
train_datagen = ImageDataGenerator(rescale=1./255, validation_split = 0.0666667)
train_generator=train_datagen.flow_from_dataframe(dataframe=train_df,
                                                  directory='X:/Flipkart GRID - Object Localization (Medium Complexity Round)/orig_data/data/images',
                                                  x_col='image_name',
                                                  y_col=['x1', 'x2', 'y1', 'y2'],
                                                  class_mode="other",
                                                  target_size = (299, 299),
                                                  batch_size=8,
                                                  shuffle = True,
                                                  subset='training')
valid_generator=train_datagen.flow_from_dataframe(dataframe=train_df,
                                                  directory='X:/Flipkart GRID - Object Localization (Medium Complexity Round)/orig_data/data/images',
                                                  x_col='image_name',
                                                  y_col=['x1', 'x2', 'y1', 'y2'],
                                                  class_mode="other",
                                                  target_size = (299, 299),
                                                  batch_size=8,
                                                  shuffle = True,
                                                  subset = 'validation')

Found 22400 images.
Found 1600 images.


In [13]:
STEP_SIZE_TRAIN=train_generator.n//train_generator.batch_size
STEP_SIZE_VALID=valid_generator.n//valid_generator.batch_size

In [14]:
model.compile(loss = mean_absolute_error, optimizer = optimizers.Adam(lr=0.001, beta_1=0.9, beta_2=0.999, epsilon=1e-8), metrics=[mIoU])

In [15]:
checkpoint = ModelCheckpoint(chkpt_dir, monitor='val_loss', verbose=1, save_best_only=True, save_weights_only=False, mode='auto', period=1)
early = EarlyStopping(monitor='val_loss', min_delta=0, patience=40, verbose=1, mode='auto')

In [16]:
def show_img_with_rect(img, lab):
    x1 = int(lab[0]/2.1404)
    x2 = int(lab[1]/2.1404)
    y1 = int(lab[2]/1.61)
    y2 = int(lab[3]/1.61) #
    cv2.rectangle(img,(x1,y1),(x2,y2),(0,255,0),3)
    plt.imshow(cv2.cvtColor(img, cv2.COLOR_BGR2RGB))

In [ ]:
# '''
#     lrf = LRFinder(minimum=3e-6, maximum=3e-4, step_size=(train_generator.n//train_generator.batch_size), n_epochs=4)
#     model.fit(x_train, y_train, callbacks=[lrf, ])
#     lrf.lr_graph()
#     lrf.loss_graph()
# '''
lrf = LRFinder(minimum=3e-6, maximum=3e-4, step_size=(train_generator.n//train_generator.batch_size), n_epochs=2)

In [ ]:
model.fit_generator(generator=train_generator,
                    steps_per_epoch=STEP_SIZE_TRAIN,
                    validation_data=valid_generator,
                    validation_steps=STEP_SIZE_VALID,
                    epochs=2,
                    verbose=2,
                    callbacks=[checkpoint, lrf],
                    shuffle=True)

In [ ]:
lrf.lr_graph()

In [ ]:
lrf.loss_graph()

In [17]:
schedule = SGDRScheduler(min_lr=3e-5,
                         max_lr=1e-3,
                         steps_per_epoch=STEP_SIZE_TRAIN,
                         lr_decay=0.9,
                         cycle_length=2,
                         mult_factor=1.5)

In [18]:
model.fit_generator(generator=train_generator,
                    steps_per_epoch=STEP_SIZE_TRAIN,
                    validation_data=valid_generator,
                    validation_steps=STEP_SIZE_VALID,
                    epochs=1000,
                    verbose=1,
                    callbacks=[checkpoint, schedule],
                    shuffle=True)

Epoch 1/1000


 194/2800 [=>............................] - ETA: 3:21:56 - loss: 1.3970 - mIoU: 0.984 - ETA: 1:50:15 - loss: 2.4624 - mIoU: 0.970 - ETA: 1:18:22 - loss: 2.1510 - mIoU: 0.971 - ETA: 1:02:28 - loss: 2.2633 - mIoU: 0.971 - ETA: 52:51 - loss: 2.5229 - mIoU: 0.9693  - ETA: 46:29 - loss: 2.6486 - mIoU: 0.968 - ETA: 41:52 - loss: 2.7014 - mIoU: 0.966 - ETA: 38:28 - loss: 2.5613 - mIoU: 0.968 - ETA: 35:49 - loss: 2.6007 - mIoU: 0.967 - ETA: 33:42 - loss: 2.8338 - mIoU: 0.962 - ETA: 31:57 - loss: 2.9066 - mIoU: 0.960 - ETA: 30:29 - loss: 2.8933 - mIoU: 0.961 - ETA: 29:16 - loss: 2.9399 - mIoU: 0.961 - ETA: 28:13 - loss: 2.9108 - mIoU: 0.961 - ETA: 27:18 - loss: 2.9796 - mIoU: 0.961 - ETA: 26:30 - loss: 4.0372 - mIoU: 0.953 - ETA: 25:48 - loss: 3.9021 - mIoU: 0.955 - ETA: 25:09 - loss: 3.7969 - mIoU: 0.956 - ETA: 24:36 - loss: 3.7641 - mIoU: 0.956 - ETA: 24:04 - loss: 3.7524 - mIoU: 0.956 - ETA: 23:37 - loss: 3.7584 - mIoU: 0.956 - ETA: 23:10 - loss: 3.6994 - mIoU: 0.957 - ETA: 22:47 - loss: 3.

 976/2800 [=========>....................] - ETA: 10:47 - loss: 4.4120 - mIoU: 0.948 - ETA: 10:47 - loss: 4.4115 - mIoU: 0.948 - ETA: 10:47 - loss: 4.4095 - mIoU: 0.948 - ETA: 10:46 - loss: 4.4073 - mIoU: 0.948 - ETA: 10:46 - loss: 4.4056 - mIoU: 0.948 - ETA: 10:46 - loss: 4.4025 - mIoU: 0.948 - ETA: 10:45 - loss: 4.4051 - mIoU: 0.948 - ETA: 10:45 - loss: 4.4034 - mIoU: 0.948 - ETA: 10:45 - loss: 4.4035 - mIoU: 0.948 - ETA: 10:44 - loss: 4.4016 - mIoU: 0.948 - ETA: 10:44 - loss: 4.4017 - mIoU: 0.948 - ETA: 10:44 - loss: 4.4008 - mIoU: 0.948 - ETA: 10:43 - loss: 4.3980 - mIoU: 0.948 - ETA: 10:43 - loss: 4.4009 - mIoU: 0.948 - ETA: 10:43 - loss: 4.4005 - mIoU: 0.948 - ETA: 10:42 - loss: 4.4009 - mIoU: 0.948 - ETA: 10:42 - loss: 4.4007 - mIoU: 0.948 - ETA: 10:42 - loss: 4.4006 - mIoU: 0.948 - ETA: 10:41 - loss: 4.3987 - mIoU: 0.948 - ETA: 10:41 - loss: 4.3961 - mIoU: 0.948 - ETA: 10:41 - loss: 4.4039 - mIoU: 0.948 - ETA: 10:40 - loss: 4.4041 - mIoU: 0.948 - ETA: 10:40 - loss: 4.4033 - mIo

1180/2800 [===========>..................] - ETA: 9:43 - loss: 4.3715 - mIoU: 0.94 - ETA: 9:42 - loss: 4.3710 - mIoU: 0.94 - ETA: 9:42 - loss: 4.3705 - mIoU: 0.94 - ETA: 9:42 - loss: 4.3696 - mIoU: 0.94 - ETA: 9:41 - loss: 4.3717 - mIoU: 0.94 - ETA: 9:41 - loss: 4.3701 - mIoU: 0.94 - ETA: 9:41 - loss: 4.3710 - mIoU: 0.94 - ETA: 9:40 - loss: 4.3694 - mIoU: 0.94 - ETA: 9:40 - loss: 4.3674 - mIoU: 0.94 - ETA: 9:40 - loss: 4.3670 - mIoU: 0.94 - ETA: 9:39 - loss: 4.3658 - mIoU: 0.94 - ETA: 9:39 - loss: 4.3649 - mIoU: 0.94 - ETA: 9:39 - loss: 4.3627 - mIoU: 0.94 - ETA: 9:38 - loss: 4.3647 - mIoU: 0.94 - ETA: 9:38 - loss: 4.3628 - mIoU: 0.94 - ETA: 9:38 - loss: 4.3619 - mIoU: 0.94 - ETA: 9:37 - loss: 4.3667 - mIoU: 0.94 - ETA: 9:37 - loss: 4.3654 - mIoU: 0.94 - ETA: 9:37 - loss: 4.3651 - mIoU: 0.94 - ETA: 9:36 - loss: 4.3643 - mIoU: 0.94 - ETA: 9:36 - loss: 4.3626 - mIoU: 0.94 - ETA: 9:36 - loss: 4.3621 - mIoU: 0.94 - ETA: 9:35 - loss: 4.3622 - mIoU: 0.94 - ETA: 9:35 - loss: 4.3610 - mIoU: 0.

1384/2800 [=============>................] - ETA: 8:36 - loss: 4.4537 - mIoU: 0.94 - ETA: 8:36 - loss: 4.4524 - mIoU: 0.94 - ETA: 8:36 - loss: 4.4521 - mIoU: 0.94 - ETA: 8:36 - loss: 4.4504 - mIoU: 0.94 - ETA: 8:35 - loss: 4.4497 - mIoU: 0.94 - ETA: 8:35 - loss: 4.4489 - mIoU: 0.94 - ETA: 8:35 - loss: 4.4510 - mIoU: 0.94 - ETA: 8:34 - loss: 4.4491 - mIoU: 0.94 - ETA: 8:34 - loss: 4.4483 - mIoU: 0.94 - ETA: 8:34 - loss: 4.4471 - mIoU: 0.94 - ETA: 8:33 - loss: 4.4620 - mIoU: 0.94 - ETA: 8:33 - loss: 4.4606 - mIoU: 0.94 - ETA: 8:33 - loss: 4.4597 - mIoU: 0.94 - ETA: 8:32 - loss: 4.4583 - mIoU: 0.94 - ETA: 8:32 - loss: 4.4649 - mIoU: 0.94 - ETA: 8:32 - loss: 4.4641 - mIoU: 0.94 - ETA: 8:31 - loss: 4.4638 - mIoU: 0.94 - ETA: 8:31 - loss: 4.4629 - mIoU: 0.94 - ETA: 8:31 - loss: 4.4617 - mIoU: 0.94 - ETA: 8:30 - loss: 4.4661 - mIoU: 0.94 - ETA: 8:30 - loss: 4.4659 - mIoU: 0.94 - ETA: 8:30 - loss: 4.4657 - mIoU: 0.94 - ETA: 8:29 - loss: 4.4644 - mIoU: 0.94 - ETA: 8:29 - loss: 4.4638 - mIoU: 0.

...

2000/2800 [====================>.........] - ETA: 5:12 - loss: 1.1019 - mIoU: 0.98 - ETA: 5:12 - loss: 1.1021 - mIoU: 0.98 - ETA: 5:12 - loss: 1.1019 - mIoU: 0.98 - ETA: 5:11 - loss: 1.1017 - mIoU: 0.98 - ETA: 5:11 - loss: 1.1015 - mIoU: 0.98 - ETA: 5:11 - loss: 1.1014 - mIoU: 0.98 - ETA: 5:10 - loss: 1.1014 - mIoU: 0.98 - ETA: 5:10 - loss: 1.1015 - mIoU: 0.98 - ETA: 5:10 - loss: 1.1013 - mIoU: 0.98 - ETA: 5:10 - loss: 1.1015 - mIoU: 0.98 - ETA: 5:09 - loss: 1.1015 - mIoU: 0.98 - ETA: 5:09 - loss: 1.1016 - mIoU: 0.98 - ETA: 5:09 - loss: 1.1012 - mIoU: 0.98 - ETA: 5:08 - loss: 1.1013 - mIoU: 0.98 - ETA: 5:08 - loss: 1.1041 - mIoU: 0.98 - ETA: 5:08 - loss: 1.1040 - mIoU: 0.98 - ETA: 5:07 - loss: 1.1037 - mIoU: 0.98 - ETA: 5:07 - loss: 1.1035 - mIoU: 0.98 - ETA: 5:07 - loss: 1.1032 - mIoU: 0.98 - ETA: 5:06 - loss: 1.1031 - mIoU: 0.98 - ETA: 5:06 - loss: 1.1030 - mIoU: 0.98 - ETA: 5:06 - loss: 1.1028 - mIoU: 0.98 - ETA: 5:06 - loss: 1.1026 - mIoU: 0.98 - ETA: 5:05 - loss: 1.1024 - mIoU: 0.

2204/2800 [======================>.......] - ETA: 4:09 - loss: 1.0940 - mIoU: 0.98 - ETA: 4:08 - loss: 1.0938 - mIoU: 0.98 - ETA: 4:08 - loss: 1.0936 - mIoU: 0.98 - ETA: 4:08 - loss: 1.0933 - mIoU: 0.98 - ETA: 4:08 - loss: 1.0931 - mIoU: 0.98 - ETA: 4:07 - loss: 1.0931 - mIoU: 0.98 - ETA: 4:07 - loss: 1.0928 - mIoU: 0.98 - ETA: 4:07 - loss: 1.0926 - mIoU: 0.98 - ETA: 4:06 - loss: 1.0929 - mIoU: 0.98 - ETA: 4:06 - loss: 1.0929 - mIoU: 0.98 - ETA: 4:06 - loss: 1.0926 - mIoU: 0.98 - ETA: 4:05 - loss: 1.0924 - mIoU: 0.98 - ETA: 4:05 - loss: 1.0922 - mIoU: 0.98 - ETA: 4:05 - loss: 1.0920 - mIoU: 0.98 - ETA: 4:04 - loss: 1.0921 - mIoU: 0.98 - ETA: 4:04 - loss: 1.0922 - mIoU: 0.98 - ETA: 4:04 - loss: 1.0925 - mIoU: 0.98 - ETA: 4:03 - loss: 1.0933 - mIoU: 0.98 - ETA: 4:03 - loss: 1.0932 - mIoU: 0.98 - ETA: 4:03 - loss: 1.0931 - mIoU: 0.98 - ETA: 4:03 - loss: 1.0930 - mIoU: 0.98 - ETA: 4:02 - loss: 1.0928 - mIoU: 0.98 - ETA: 4:02 - loss: 1.0934 - mIoU: 0.98 - ETA: 4:02 - loss: 1.0934 - mIoU: 0.

2408/2800 [========================>.....] - ETA: 3:05 - loss: 1.0877 - mIoU: 0.98 - ETA: 3:05 - loss: 1.0875 - mIoU: 0.98 - ETA: 3:05 - loss: 1.0876 - mIoU: 0.98 - ETA: 3:04 - loss: 1.0874 - mIoU: 0.98 - ETA: 3:04 - loss: 1.0875 - mIoU: 0.98 - ETA: 3:04 - loss: 1.0873 - mIoU: 0.98 - ETA: 3:03 - loss: 1.0870 - mIoU: 0.98 - ETA: 3:03 - loss: 1.0868 - mIoU: 0.98 - ETA: 3:03 - loss: 1.0867 - mIoU: 0.98 - ETA: 3:02 - loss: 1.0872 - mIoU: 0.98 - ETA: 3:02 - loss: 1.0871 - mIoU: 0.98 - ETA: 3:02 - loss: 1.0869 - mIoU: 0.98 - ETA: 3:01 - loss: 1.0869 - mIoU: 0.98 - ETA: 3:01 - loss: 1.0867 - mIoU: 0.98 - ETA: 3:01 - loss: 1.0865 - mIoU: 0.98 - ETA: 3:00 - loss: 1.0864 - mIoU: 0.98 - ETA: 3:00 - loss: 1.0862 - mIoU: 0.98 - ETA: 3:00 - loss: 1.0860 - mIoU: 0.98 - ETA: 3:00 - loss: 1.0860 - mIoU: 0.98 - ETA: 2:59 - loss: 1.0857 - mIoU: 0.98 - ETA: 2:59 - loss: 1.0855 - mIoU: 0.98 - ETA: 2:59 - loss: 1.0852 - mIoU: 0.98 - ETA: 2:58 - loss: 1.0853 - mIoU: 0.98 - ETA: 2:58 - loss: 1.0851 - mIoU: 0.

2493/2800 [=========================>....] - ETA: 2:01 - loss: 1.0741 - mIoU: 0.98 - ETA: 2:01 - loss: 1.0739 - mIoU: 0.98 - ETA: 2:01 - loss: 1.0738 - mIoU: 0.98 - ETA: 2:01 - loss: 1.0738 - mIoU: 0.98 - ETA: 2:00 - loss: 1.0736 - mIoU: 0.98 - ETA: 2:00 - loss: 1.0735 - mIoU: 0.98 - ETA: 2:00 - loss: 1.0734 - mIoU: 0.98 - ETA: 1:59 - loss: 1.0732 - mIoU: 0.98 - ETA: 1:59 - loss: 1.0733 - mIoU: 0.98 - ETA: 1:59 - loss: 1.0732 - mIoU: 0.98 - ETA: 1:58 - loss: 1.0733 - mIoU: 0.98 - ETA: 1:58 - loss: 1.0731 - mIoU: 0.98 - ETA: 1:58 - loss: 1.0730 - mIoU: 0.98 - ETA: 1:57 - loss: 1.0749 - mIoU: 0.98 - ETA: 1:57 - loss: 1.0749 - mIoU: 0.98 - ETA: 1:57 - loss: 1.0747 - mIoU: 0.98 - ETA: 1:56 - loss: 1.0748 - mIoU: 0.98 - ETA: 1:56 - loss: 1.0774 - mIoU: 0.98 - ETA: 1:56 - loss: 1.0773 - mIoU: 0.98 - ETA: 1:56 - loss: 1.0772 - mIoU: 0.98 - ETA: 1:55 - loss: 1.0772 - mIoU: 0.98 - ETA: 1:55 - loss: 1.0770 - mIoU: 0.98 - ETA: 1:55 - loss: 1.0769 - mIoU: 0.98 - ETA: 1:54 - loss: 1.0768 - mIoU: 0.

KeyboardInterrupt: 

In [19]:
model.save('xception_lrf_trained_val_tr98_95.h5')